In [2]:
#imports
library(readr)
library(fgsea)
library(pathwayPCA)
suppressMessages(library(tigerstats))
suppressMessages(library(ggplot2))
suppressMessages(library(gridExtra))
suppressMessages(library("DESeq2"))
suppressMessages(library("vsn"))
suppressMessages(library("pheatmap"))
suppressMessages(library("RColorBrewer"))
suppressMessages(library(repr))

In [7]:
library(fgsea)
library(data.table)
library(ggplot2)

In [1]:
mc <- suppressMessages(read_tsv("morphological-counts.tsv"))
rna <- suppressMessages(read_tsv("RNA-read-counts.tsv"))

ERROR: Error in read_tsv("morphological-counts.tsv"): could not find function "read_tsv"


In [9]:
mc

SMPLID          Mophological.cluster.0 Mophological.cluster.1
1   GTEX-11EM3-0126  20                     22                   
2   GTEX-11EQ9-0626  51                     81                   
3   GTEX-11LCK-0526  79                     86                   
4   GTEX-11NSD-0126  45                    140                   
5   GTEX-11O72-2326 171                    139                   
6   GTEX-11P7K-0226 159                     65                   
7   GTEX-11P81-0126  86                    189                   
8   GTEX-11P82-0226  71                    122                   
9   GTEX-11TT1-1126  30                    100                   
10  GTEX-11VI4-0226 150                    121                   
11  GTEX-11XUK-0226  60                     27                   
12  GTEX-12584-0826 200                    106                   
13  GTEX-12WSE-1226 180                    243                   
14  GTEX-12WSJ-0326  89                      8                   
15  GTEX-12WSK-0926  92                     59                   
16  GTEX-12WSN-0726 160                    127                   
17  GTEX-12ZZX-1226 124                     87                   
18  GTEX-133LE-0326  97                      3                   
19  GTEX-1399R-0126  95                     69                   
20  GTEX-13FTW-0626  25                     16                   
21  GTEX-13FTY-0726 160                     83                   
22  GTEX-13NYB-0726 232                    146                   
23  GTEX-13OVK-0226  25                     29                   
24  GTEX-13PL6-1026 228                    145                   
25  GTEX-13QBU-0626  33                     33                   
26  GTEX-13RTK-0326 115                    135                   
27  GTEX-13S86-1126 122                    297                   
28  GTEX-13U4I-0526 117                     74                   
29  GTEX-13VXT-0626 133                    193                   
30  GTEX-144GM-0226  64                    108                   
⋮   ⋮               ⋮                      ⋮                     
107 GTEX-1JMPZ-0626 210                    122                   
108 GTEX-1K2DU-0126 151                    237                   
109 GTEX-1KD4Q-1026  83                    219                   
110 GTEX-1LBAC-0726  39                     38                   
111 GTEX-1LG7Z-0526  13                     30                   
112 GTEX-1MCC2-0526  32                     14                   
113 GTEX-1MGNQ-0726  54                      9                   
114 GTEX-1MJK3-0326 189                     74                   
115 GTEX-1NUQO-0926 107                    195                   
116 GTEX-1OJC3-0626 214                    650                   
117 GTEX-1PBJI-0726  90                    194                   
118 GTEX-1PBJJ-1926 108                     75                   
119 GTEX-1PDJ9-0826  71                     67                   
120 GTEX-1PFEY-0226  80                     15                   
121 GTEX-1PIGE-0726 256                    147                   
122 GTEX-1PIIG-2026 179                    235                   
123 GTEX-1PPH8-0926 155                    168                   
124 GTEX-1QCLY-0826 114                    182                   
125 GTEX-1QP67-0326 242                    172                   
126 GTEX-1QP6S-2526 312                    141                   
127 GTEX-1QP9N-0126  22                     88                   
128 GTEX-1QPFJ-0626  10                     26                   
129 GTEX-1QW4Y-0226  16                    152                   
130 GTEX-1R9JW-0226  28                     35                   
131 GTEX-1R9PM-0226 151                    389                   
132 GTEX-1RAZA-0826 138                    136                   
133 GTEX-1RAZQ-0926 138                    165                   
134 GTEX-1RAZR-1126  62                     46                   
135 GTEX-1S5ZU-0726 134                    2

In [10]:
#normalization (we use frequency instead of count)
for (i in 1:136){
    mc[i,2:65] <- mc[i,2:65]/sum(mc[i,2:65])
} 


In [11]:
#filtering the data (only take the genes in the top quartile of expression)
means <- rowMeans(rna[,3:138])
#med <- median(means)
qt <- quantile(means)[4]
cond <- means > qt
rna$cond <- cond
rna <- rna[rna$cond == TRUE,]
rna

Name               Description   GTEX-11EM3-0126 GTEX-11EQ9-0626
1     ENSG00000227232.5  WASH7P          122             174          
2     ENSG00000279457.4  RP11-34P13.18   241             388          
3     ENSG00000225972.1  MTND1P23        142             120          
4     ENSG00000225630.1  MTND2P28      12884           22597          
5     ENSG00000237973.1  MTCO1P12       3138            3534          
6     ENSG00000229344.1  MTCO2P12        470             537          
7     ENSG00000248527.1  MTATP6P1      52329           78285          
8     ENSG00000198744.5  MTCO3P12        436             782          
9     ENSG00000228327.3  RP11-206L10.2   718             682          
10    ENSG00000228794.8  LINC01128      1382            2099          
11    ENSG00000225880.5  LINC00115       126             224          
12    ENSG00000187634.11 SAMD11          476             905          
13    ENSG00000188976.10 NOC2L          3609            4555          
14    ENSG00000187961.13 KLHL17          670            1510          
15    ENSG00000272512.1  RP11-54O7.17    297             107          
16    ENSG00000188290.10 HES4            441             387          
17    ENSG00000187608.8  ISG15           458             662          
18    ENSG00000188157.14 AGRN          14883           18905          
19    ENSG00000131591.17 C1orf159       1201            1698          
20    ENSG00000272141.1  RP11-465B22.8   265             511          
21    ENSG00000186827.10 TNFRSF4         104              95          
22    ENSG00000078808.16 SDF4          11103           10551          
23    ENSG00000176022.4  B3GALT6        1223            1432          
24    ENSG00000160087.20 UBE2J2         2720            3557          
25    ENSG00000162572.20 SCNN1D          570             754          
26    ENSG00000131584.18 ACAP3          3970            7824          
27    ENSG00000169972.11 PUSL1           389             619          
28    ENSG00000127054.20 INTS11         7127           10364          
29    ENSG00000240731.1  RP5-890O3.9     234             350          
30    ENSG00000224051.6  CPTP           1399            1912          
⋮     ⋮                  ⋮             ⋮               ⋮              
14021 ENSG00000067646.11 ZFY                 0            1699        
14022 ENSG00000092377.13 TBL1Y               0             293        
14023 ENSG00000273906.1  RP11-115H13.1       0             575        
14024 ENSG00000099725.14 PRKY                5            1736        
14025 ENSG00000233864.7  TTTY15              2             361        
14026 ENSG00000114374.12 USP9Y              12            4948        
14027 ENSG00000067048.16 DDX3Y              41            7361        
14028 ENSG00000183878.15 UTY                 6            2140        
14029 ENSG00000165246.13 NLGN4Y              2             217        
14030 ENSG00000176728.7  TTTY14              0             502        
14031 ENSG00000131002.11 TXLNGY              7            4868        
14032 ENSG00000260197.1  RP11-424G14.1       0             607        
14033 ENSG00000012817.15 KDM5D              16           10617        
14034 ENSG00000198692.9  EIF1AY              2            1232        
14035 ENSG00000211459.2  MT-RNR1         35074           30998        
14036 ENSG00000210082.2  MT-RNR2        331376          348709        
14037 ENSG00000198888.2  MT-ND1         462445          604525        
14038 ENSG00000198763.3  MT-ND2         401331          644517        
14039 ENSG00000198804.2  MT-CO1        1746814         1998165        
14040 ENSG00000210151.2  MT-TS1            229             147        
14041 ENSG00000198712.1  MT-CO2         563143         1064812        
14042 ENSG00000228253.1  MT-ATP8         96445          140219        
14043 ENSG00000198899.2  MT-ATP6        550091          740166        
14044 ENSG00000198938.2  MT-CO3         591693          995376        
14045 ENSG00000198840.2  MT-ND

In [57]:
#change the structure of the dataset to have the gene names as the row names
dataset = data.frame(rna[, 3:138])
row.names(dataset) <- t(rna[1:14050,1])
head(dataset)

GTEX.11EM3.0126 GTEX.11EQ9.0626 GTEX.11LCK.0526
ENSG00000227232.5   122             174             85           
ENSG00000279457.4   241             388             84           
ENSG00000225972.1   142             120             76           
ENSG00000225630.1 12884           22597           9366           
ENSG00000237973.1  3138            3534           1719           
ENSG00000229344.1   470             537            255           
                  GTEX.11NSD.0126 GTEX.11O72.2326 GTEX.11P7K.0226
ENSG00000227232.5  115              197             263          
ENSG00000279457.4  370              368             156          
ENSG00000225972.1  125               45           21804          
ENSG00000225630.1 9301            19615            7169          
ENSG00000237973.1 3210              405            7076          
ENSG00000229344.1  934              159             361          
                  GTEX.11P81.0126 GTEX.11P82.0226 GTEX.11TT1.1126
ENSG00000227232.5  119              125             103          
ENSG00000279457.4  303              141             411          
ENSG00000225972.1   41               70              72          
ENSG00000225630.1 9587            18815           13056          
ENSG00000237973.1  570             3186            3285          
ENSG00000229344.1  107              230             221          
                  GTEX.11VI4.0226 ⋯ GTEX.1QP9N.0126 GTEX.1QPFJ.0626
ENSG00000227232.5  135            ⋯  111              183          
ENSG00000279457.4  297            ⋯  590              291          
ENSG00000225972.1   28            ⋯   38               29          
ENSG00000225630.1 7859            ⋯ 6884            14655          
ENSG00000237973.1 1711            ⋯ 1918             1384          
ENSG00000229344.1  116            ⋯  134               86          
                  GTEX.1QW4Y.0226 GTEX.1R9JW.0226 GTEX.1R9PM.0226
ENSG00000227232.5   124             74             191           
ENSG00000279457.4   422            336             288           
ENSG00000225972.1    29             25              20           
ENSG00000225630.1 10444           6079            7345           
ENSG00000237973.1  1431           1034            2473           
ENSG00000229344.1    95            119              66           
                  GTEX.1RAZA.0826 GTEX.1RAZQ.0926 GTEX.1RAZR.1126
ENSG00000227232.5   251             246             91           
ENSG00000279457.4   366             267            235           
ENSG00000225972.1    44              59             28           
ENSG00000225630.1 16137           12594           7127           
ENSG00000237973.1  2497            1311            835           
ENSG00000229344.1   179             131             33           
                  GTEX.1S5ZU.0726 GTEX.1S83E.0726
ENSG00000227232.5  169              162          
ENSG00000279457.4  240              454          
ENSG00000225972.1   38               42          
ENSG00000225630.1 7727            10520          
ENSG00000237973.1  390             1730          
ENSG00000229344.1   98              177

In [13]:
cluster_table_rowlg <- length(rownames(dataset))
cluster_table_rowlg

[1] 14050

In [14]:
#test of differential expression computation with cluster 4
dds = DESeqDataSetFromMatrix(dataset,colData=mc, design = ~ Mophological.cluster.4)
dds <- DESeq(dds)
dds <- DESeq(dds, quiet=TRUE)
print(resultsNames(dds))
res <- results(dds)
res.05 <- results(dds, alpha = 0.05)
resSig <- subset(res, padj < 0.05)
print(rownames(resSig))

converting counts to integer mode

estimating size factors

estimating dispersions

gene-wise dispersion estimates

mean-dispersion relationship

final dispersion estimates

fitting model and testing



[1] "Intercept"              "Mophological.cluster.4"
   [1] "ENSG00000237973.1"  "ENSG00000228327.3"  "ENSG00000225880.5" 
   [4] "ENSG00000162572.20" "ENSG00000169972.11" "ENSG00000149527.17"
   [7] "ENSG00000238164.6"  "ENSG00000157873.17" "ENSG00000130764.9" 
  [10] "ENSG00000069424.14" "ENSG00000116237.15" "ENSG00000215788.9" 
  [13] "ENSG00000162426.14" "ENSG00000162441.11" "ENSG00000173614.13"
  [16] "ENSG00000162444.11" "ENSG00000175206.10" "ENSG00000028137.18"
  [19] "ENSG00000184908.17" "ENSG00000142632.16" "ENSG00000117118.9" 
  [22] "ENSG00000179023.8"  "ENSG00000162543.5"  "ENSG00000090432.6" 
  [25] "ENSG00000169641.13" "ENSG00000188529.14" "ENSG00000020633.18"
  [28] "ENSG00000169442.8"  "ENSG00000204160.11" "ENSG00000142784.15"
  [31] "ENSG00000117751.17" "ENSG00000130775.15" "ENSG00000130772.13"
  [34] "ENSG00000197989.13" "ENSG00000198492.15" "ENSG00000116350.16"
  [37] "ENSG00000182866.16" "ENSG00000121903.14" "ENSG00000092850.11"
  [40] "ENSG00000116871.15" "ENSG000

In [15]:
res
res$log2FoldChange

log2 fold change (MLE): Mophological.cluster.4 
Wald test p-value: Mophological.cluster.4 
DataFrame with 14050 rows and 6 columns
                   baseMean log2FoldChange     lfcSE       stat      pvalue
                  <numeric>      <numeric> <numeric>  <numeric>   <numeric>
ENSG00000227232.5   188.322       2.415753   2.98346  0.8097145 4.18104e-01
ENSG00000279457.4   360.692       3.288385   2.32433  1.4147665 1.57137e-01
ENSG00000225972.1  1673.862     -30.000000  12.66222 -2.3692536 1.78240e-02
ENSG00000225630.1 13771.356       0.251998   3.50657  0.0718646 9.42710e-01
ENSG00000237973.1  3216.798     -30.369483   6.61011 -4.5944017 4.33993e-06
...                     ...            ...       ...        ...         ...
ENSG00000212907.2   99343.9       -4.36318   2.90978   -1.49949  0.13374654
ENSG00000198886.2  969909.5       -3.81706   2.92771   -1.30377  0.19231242
ENSG00000198786.2  198308.1       -9.77217   4.56354   -2.14136  0.03224523
ENSG00000198695.2   59198.3      

[1]  2.415753e+00  3.288385e+00 -3.000000e+01  2.519979e-01 -3.036948e+01
    [6] -2.227622e+00 -2.667817e+00  5.448971e+00  6.596877e+00  3.507306e-01
   [11]  7.824926e+00  9.849838e+00  9.554977e-01  2.649772e-01  1.177110e+00
   [16]  4.813446e+00  8.825112e+00 -1.394786e+00  4.702374e+00 -3.341803e+00
   [21] -7.288247e-01 -1.540002e+00 -4.026037e+00 -7.276050e-01  8.018823e+00
   [26]  6.192254e-01 -3.944062e+00  2.521988e+00  8.829066e-03 -1.254020e-02
   [31]  1.930691e+00  8.941063e-01 -2.963899e+00  3.970684e+00 -2.145413e+00
   [36] -2.985802e+00  3.270514e+00  6.450905e+00 -1.532491e+00  6.005725e-01
   [41]  2.639112e+00 -1.413775e+00  8.175370e-03  3.974651e+00  1.158002e+00
   [46]  2.159644e+00  2.513431e+00 -2.031803e+00  3.059854e+00  2.309269e+00
   [51]  1.253385e+00 -3.584033e+00  9.897343e-01 -1.024300e+00 -2.685862e+00
   [56] -3.549185e+00  7.484563e-01  4.307927e-01  3.439872e+00  2.392336e+00
   [61] -1.096773e+00  3.485385e-01  2.227977e+01 -1.445277e+00  1.498767e+01
   [66]  7.500088e+00 -3.822854e-02  4.861924e+00  1.888022e+00 -3.660436e+00
   [71] -1.413181e+00 -3.555502e-01 -1.859522e+00  1.576062e+00  2.364318e+00
   [76]  1.706396e+00 -3.526742e+00 -5.870639e-01  6.103435e-01  1.389811e-01
   [81]  2.180833e+00 -1.390590e+00  1.223334e+01  1.835428e+00  2.831801e+00
   [86] -4.210999e+00 -3.121201e+00 -6.715895e-01  9.906803e+00  3.583312e+00
   [91] -2.664285e+00  1.399786e+00  1.441165e+00  3.966902e+00 -2.986773e-01
   [96] -1.721873e+00  1.158930e+00  1.094043e+00  7.269083e+00 -3.965891e+00
  [101]  7.575135e+00 -6.949933e+00  9.583614e-01 -5.096379e+00 -3.295392e+00
  [106] -1.119405e+00  8.165137e-01  3.142659e+00 -1.910986e+00 -1.440798e+00
  [111]  9.926000e+00  4.930274e-01 -1.043669e+00 -4.156457e+00 -4.439854e+00
  [116]  8.074776e+00 -6.597458e-02  4.002848e-01 -3.167376e+00 -1.541929e+00
  [121] -1.287944e+00  1.662993e-01  1.517939e+00  1.492058e+00 -1.732965e+00
  [126]  3.214053e+00 -2.854429e+00  2.160857e+00  3.376338e+00 -2.266417e+00
  [131] -2.592460e+00 -2.595079e-01  4.347130e+00  3.979837e+00  4.835097e+00
  [136] -1.458873e-01 -1.571105e+00  2.916224e+00 -3.000000e+01 -1.813205e-02
  [141] -1.723021e+00  1.266589e-01  9.151419e-01  1.034187e+01  8.705513e-02
  [146]  2.301144e+00 -3.626862e+00  2.314560e+00 -1.476442e+00  1.016924e+00
  [151]  1.916490e+00 -2.094238e-01 -1.523704e+00  1.314333e+00  2.057146e+00
  [156]  3.601249e+00 -3.092256e-01  9.344219e-01  5.853273e-01  1.069975e+00
  [161]  3.426993e+00 -6.100837e+00  3.637560e+00  1.172794e+01 -3.195924e+00
  [166] -6.286131e+00  5.629536e+00  1.487595e+00 -3.666273e-01 -1.170730e+00
  [171] -5.911149e-02  6.237668e-01  4.809995e-01 -3.317724e+00  2.459497e+00
  [176]  8.386021e-01  7.565113e-01  3.195301e+00 -3.731280e+00  1.478472e-01
  [181] -4.937616e+00  1.028053e+00  1.561489e+00 -1.434123e+01 -5.447885e+00
  [186]  9.949488e-01  1.504660e+00 -1.792105e+00 -8.750176e-01 -1.923739e+00
  [191]  9.077560e-01 -9.765293e-01 -3.460366e+00  2.880234e+00  5.002417e-01
  [196]  4.663188e-01 -1.037786e+01  1.160140e+01  7.576962e-01 -5.194957e+00
  [201] -2.021925e+00 -1.276157e+00 -1.617433e+00 -2.120822e+00  5.447389e-01
  [206] -1.698145e+00 -5.477602e-01 -8.164280e-01  1.034817e+00  1.414001e+00
  [211] -8.518561e-01 -1.040884e+00  6.120825e+00 -3.532934e-01  8.972561e-01
  [216] -2.862823e+00 -5.242288e+00  3.432124e-01 -1.282703e+01 -1.216194e+01
  [221] -1.424723e+01 -7.122175e+00 -9.126396e-01 -3.616995e+00  5.218742e+00
  [226]  5.257677e-01 -4.080527e+00  5.327582e+00  3.806613e+00  1.375883e+00
  [231] -3.692206e+00  2.881236e+00 -2.405400e+00 -7.327086e-01 -3.657263e-01
  [236]  7.187169e-01 -7.967285e-01 -1.110609e+00  3.895915e+00  4.343679e+00
  [241]  1.022042e+00 -2.633197e-01 -8.655271e-01  2.654248e+00  2.330875e+00
  [246]  3.955726e-01  1.680516e-01  2.656572e+01  1.218488e+00  4.746868e+00
  [251] -1.639355e+00  9.917007e-01  8.831901e-01  6.951856e-01 -6.148155e-01
  [256] -1.096311e+00 -2.4

In [16]:
print(rownames(dataset))

    [1] "ENSG00000227232.5"  "ENSG00000279457.4"  "ENSG00000225972.1" 
    [4] "ENSG00000225630.1"  "ENSG00000237973.1"  "ENSG00000229344.1" 
    [7] "ENSG00000248527.1"  "ENSG00000198744.5"  "ENSG00000228327.3" 
   [10] "ENSG00000228794.8"  "ENSG00000225880.5"  "ENSG00000187634.11"
   [13] "ENSG00000188976.10" "ENSG00000187961.13" "ENSG00000272512.1" 
   [16] "ENSG00000188290.10" "ENSG00000187608.8"  "ENSG00000188157.14"
   [19] "ENSG00000131591.17" "ENSG00000272141.1"  "ENSG00000186827.10"
   [22] "ENSG00000078808.16" "ENSG00000176022.4"  "ENSG00000160087.20"
   [25] "ENSG00000162572.20" "ENSG00000131584.18" "ENSG00000169972.11"
   [28] "ENSG00000127054.20" "ENSG00000240731.1"  "ENSG00000224051.6" 
   [31] "ENSG00000107404.19" "ENSG00000162576.16" "ENSG00000175756.13"
   [34] "ENSG00000221978.11" "ENSG00000224870.6"  "ENSG00000242485.5" 
   [37] "ENSG00000272455.1"  "ENSG00000235098.8"  "ENSG00000179403.11"
   [40] "ENSG00000215915.9"  "ENSG00000160072.19" "ENSG00000197785.13"
   [43

In [17]:
#cluster_table va être une matrice pour les resultats 
row <- rownames(dataset)
#row <- row[-6]
col <- colnames(mc[,2:65])


cluster_table <- data.frame(matrix(ncol = 64, nrow = cluster_table_rowlg))
colnames(cluster_table) <- col
rownames(cluster_table) <- row
cluster_table
print(row)

Mophological.cluster.0 Mophological.cluster.1
ENSG00000227232.5  NA                     NA                    
ENSG00000279457.4  NA                     NA                    
ENSG00000225972.1  NA                     NA                    
ENSG00000225630.1  NA                     NA                    
ENSG00000237973.1  NA                     NA                    
ENSG00000229344.1  NA                     NA                    
ENSG00000248527.1  NA                     NA                    
ENSG00000198744.5  NA                     NA                    
ENSG00000228327.3  NA                     NA                    
ENSG00000228794.8  NA                     NA                    
ENSG00000225880.5  NA                     NA                    
ENSG00000187634.11 NA                     NA                    
ENSG00000188976.10 NA                     NA                    
ENSG00000187961.13 NA                     NA                    
ENSG00000272512.1  NA                     NA                    
ENSG00000188290.10 NA                     NA                    
ENSG00000187608.8  NA                     NA                    
ENSG00000188157.14 NA                     NA                    
ENSG00000131591.17 NA                     NA                    
ENSG00000272141.1  NA                     NA                    
ENSG00000186827.10 NA                     NA                    
ENSG00000078808.16 NA                     NA                    
ENSG00000176022.4  NA                     NA                    
ENSG00000160087.20 NA                     NA                    
ENSG00000162572.20 NA                     NA                    
ENSG00000131584.18 NA                     NA                    
ENSG00000169972.11 NA                     NA                    
ENSG00000127054.20 NA                     NA                    
ENSG00000240731.1  NA                     NA                    
ENSG00000224051.6  NA                     NA                    
⋮                  ⋮                      ⋮                     
ENSG00000067646.11 NA                     NA                    
ENSG00000092377.13 NA                     NA                    
ENSG00000273906.1  NA                     NA                    
ENSG00000099725.14 NA                     NA                    
ENSG00000233864.7  NA                     NA                    
ENSG00000114374.12 NA                     NA                    
ENSG00000067048.16 NA                     NA                    
ENSG00000183878.15 NA                     NA                    
ENSG00000165246.13 NA                     NA                    
ENSG00000176728.7  NA                     NA                    
ENSG00000131002.11 NA                     NA                    
ENSG00000260197.1  NA                     NA                    
ENSG00000012817.15 NA                     NA                    
ENSG00000198692.9  NA                     NA                    
ENSG00000211459.2  NA                     NA                    
ENSG00000210082.2  NA                     NA                    
ENSG00000198888.2  NA                     NA                    
ENSG00000198763.3  NA                     NA                    
ENSG00000198804.2  NA                     NA                    
ENSG00000210151.2  NA                     NA                    
ENSG00000198712.1  NA                     NA                    
ENSG00000228253.1  NA                     NA                    
ENSG00000198899.2  NA                     NA                    
ENSG00000198938.2  NA                     NA                    
ENSG00000198840.2  NA                     NA                    
ENSG00000212907.2  NA                     NA                    
ENSG00000198886.2  NA                     NA                    
ENSG00000198786.2  NA                     NA                    
ENSG00000198695.2  NA                     NA                    
ENSG00000198727.2  NA                     NA          

    [1] "ENSG00000227232.5"  "ENSG00000279457.4"  "ENSG00000225972.1" 
    [4] "ENSG00000225630.1"  "ENSG00000237973.1"  "ENSG00000229344.1" 
    [7] "ENSG00000248527.1"  "ENSG00000198744.5"  "ENSG00000228327.3" 
   [10] "ENSG00000228794.8"  "ENSG00000225880.5"  "ENSG00000187634.11"
   [13] "ENSG00000188976.10" "ENSG00000187961.13" "ENSG00000272512.1" 
   [16] "ENSG00000188290.10" "ENSG00000187608.8"  "ENSG00000188157.14"
   [19] "ENSG00000131591.17" "ENSG00000272141.1"  "ENSG00000186827.10"
   [22] "ENSG00000078808.16" "ENSG00000176022.4"  "ENSG00000160087.20"
   [25] "ENSG00000162572.20" "ENSG00000131584.18" "ENSG00000169972.11"
   [28] "ENSG00000127054.20" "ENSG00000240731.1"  "ENSG00000224051.6" 
   [31] "ENSG00000107404.19" "ENSG00000162576.16" "ENSG00000175756.13"
   [34] "ENSG00000221978.11" "ENSG00000224870.6"  "ENSG00000242485.5" 
   [37] "ENSG00000272455.1"  "ENSG00000235098.8"  "ENSG00000179403.11"
   [40] "ENSG00000215915.9"  "ENSG00000160072.19" "ENSG00000197785.13"
   [43

In [21]:
#fonction pour remplir la ligne du tableau 'cluster_table'

num_dif_exp_cluster_table <- function(condition){
    cond <- as.formula(paste("~", condition))
    print(cond)
    dds = DESeqDataSetFromMatrix(dataset,colData=mc, design = cond)
    dds <- DESeq(dds, quiet=TRUE)
    print(resultsNames(dds))
    res <- results(dds)
    lfc = res$log2FoldChange
    cluster_table[condition] <<- lfc
    res.05 <- results(dds, alpha = 0.05)
    resSig <- subset(res, padj < 0.05)
    print(rownames(resSig))
}

In [ ]:
num_dif_exp( "Mophological.cluster.4")

In [ ]:
num_dif_exp( "Mophological.cluster.5")

In [ ]:
cluster_table

In [19]:
print(col)

 [1] "Mophological.cluster.0"  "Mophological.cluster.1" 
 [3] "Mophological.cluster.2"  "Mophological.cluster.3" 
 [5] "Mophological.cluster.4"  "Mophological.cluster.5" 
 [7] "Mophological.cluster.6"  "Mophological.cluster.7" 
 [9] "Mophological.cluster.8"  "Mophological.cluster.9" 
[11] "Mophological.cluster.10" "Mophological.cluster.11"
[13] "Mophological.cluster.12" "Mophological.cluster.13"
[15] "Mophological.cluster.14" "Mophological.cluster.15"
[17] "Mophological.cluster.16" "Mophological.cluster.17"
[19] "Mophological.cluster.18" "Mophological.cluster.19"
[21] "Mophological.cluster.20" "Mophological.cluster.21"
[23] "Mophological.cluster.22" "Mophological.cluster.23"
[25] "Mophological.cluster.24" "Mophological.cluster.25"
[27] "Mophological.cluster.26" "Mophological.cluster.27"
[29] "Mophological.cluster.28" "Mophological.cluster.29"
[31] "Mophological.cluster.30" "Mophological.cluster.31"
[33] "Mophological.cluster.32" "Mophological.cluster.33"
[35] "Mophological.cluster.34" 

In [23]:
#to do : loop for num_diff_exp
#for(variable in numerical_variables){
#    num_dif_exp(variable, assoc_table)}

#for (r in 1:R){
#x=runif(N,-1,1)
#Y=array(sin(x)+rnorm(N,sqrt(0.5)),c(N,1))
#X=cbind(numeric(N)+1,x)
#betahat=solve(t(X)%*%X) %*%t(X)%*%Y
#xq=array(c(1,0),c(2,1))
#Yhat=c(Yhat,t(xq)%*%betahat)
#X2=cbind(numeric(N)+1,x,x^2)
#betahat2=solve(t(X2)%*%X2) %*%t(X2)%*%Y
#xq=array(c(1,0,0),c(3,1))
#Yhat2=c(Yhat2,t(xq)%*%betahat2)
#}


for (i in col){
    num_dif_exp(i)
}

~Mophological.cluster.0
<environment: 0x56022ef6af48>


converting counts to integer mode



[1] "Intercept"              "Mophological.cluster.0"
   [1] "ENSG00000227232.5"  "ENSG00000279457.4"  "ENSG00000237973.1" 
   [4] "ENSG00000225880.5"  "ENSG00000187608.8"  "ENSG00000176022.4" 
   [7] "ENSG00000160087.20" "ENSG00000162572.20" "ENSG00000127054.20"
  [10] "ENSG00000221978.11" "ENSG00000224870.6"  "ENSG00000242485.5" 
  [13] "ENSG00000197530.12" "ENSG00000116151.13" "ENSG00000269896.2" 
  [16] "ENSG00000157916.19" "ENSG00000177133.10" "ENSG00000227372.11"
  [19] "ENSG00000130764.9"  "ENSG00000069424.14" "ENSG00000116251.9" 
  [22] "ENSG00000158286.12" "ENSG00000162408.10" "ENSG00000204859.12"
  [25] "ENSG00000116273.5"  "ENSG00000041988.15" "ENSG00000007923.15"
  [28] "ENSG00000171735.18" "ENSG00000116285.12" "ENSG00000074800.13"
  [31] "ENSG00000049239.12" "ENSG00000178585.14" "ENSG00000142657.20"
  [34] "ENSG00000116649.9"  "ENSG00000120942.13" "ENSG00000116661.9" 
  [37] "ENSG00000132879.13" "ENSG00000132906.17" "ENSG00000162461.7" 
  [40] "ENSG00000237276.8"  "ENSG000

converting counts to integer mode



[1] "Intercept"              "Mophological.cluster.1"
   [1] "ENSG00000227232.5"  "ENSG00000229344.1"  "ENSG00000188290.10"
   [4] "ENSG00000176022.4"  "ENSG00000162572.20" "ENSG00000127054.20"
   [7] "ENSG00000224870.6"  "ENSG00000197530.12" "ENSG00000157916.19"
  [10] "ENSG00000069424.14" "ENSG00000049245.12" "ENSG00000074800.13"
  [13] "ENSG00000228526.6"  "ENSG00000142657.20" "ENSG00000271895.2" 
  [16] "ENSG00000132879.13" "ENSG00000132906.17" "ENSG00000162461.7" 
  [19] "ENSG00000117118.9"  "ENSG00000090432.6"  "ENSG00000244038.9" 
  [22] "ENSG00000173372.16" "ENSG00000159189.11" "ENSG00000173369.15"
  [25] "ENSG00000011009.10" "ENSG00000117305.14" "ENSG00000117602.11"
  [28] "ENSG00000020633.18" "ENSG00000158014.14" "ENSG00000117682.16"
  [31] "ENSG00000117676.13" "ENSG00000090020.10" "ENSG00000142765.17"
  [34] "ENSG00000142748.12" "ENSG00000130772.13" "ENSG00000159023.19"
  [37] "ENSG00000253304.1"  "ENSG00000162511.7"  "ENSG00000060688.12"
  [40] "ENSG00000168528.11" "ENSG000

...

[1] "Intercept"               "Mophological.cluster.61"
 [1] "ENSG00000182873.5"  "ENSG00000175206.10" "ENSG00000118194.18"
 [4] "ENSG00000204305.13" "ENSG00000229391.7"  "ENSG00000237541.3" 
 [7] "ENSG00000244734.3"  "ENSG00000110076.18" "ENSG00000205420.10"
[10] "ENSG00000170477.12" "ENSG00000159251.6"  "ENSG00000140465.13"
[13] "ENSG00000188536.12" "ENSG00000206172.8"  "ENSG00000171401.14"
[16] "ENSG00000197971.14" "ENSG00000088836.12" "ENSG00000277287.1" 
[19] "ENSG00000101040.19" "ENSG00000198125.12"
~Mophological.cluster.62
<environment: 0x56023816f578>


converting counts to integer mode



[1] "Intercept"               "Mophological.cluster.62"
  [1] "ENSG00000272141.1"  "ENSG00000162426.14" "ENSG00000175206.10"
  [4] "ENSG00000020633.18" "ENSG00000169442.8"  "ENSG00000162511.7" 
  [7] "ENSG00000162512.15" "ENSG00000182866.16" "ENSG00000146463.11"
 [10] "ENSG00000119535.17" "ENSG00000084070.11" "ENSG00000117480.15"
 [13] "ENSG00000097096.8"  "ENSG00000154451.14" "ENSG00000143119.12"
 [16] "ENSG00000064703.11" "ENSG00000203865.9"  "ENSG00000116824.4" 
 [19] "ENSG00000143375.14" "ENSG00000163346.16" "ENSG00000162739.13"
 [22] "ENSG00000066294.14" "ENSG00000117091.9"  "ENSG00000026751.16"
 [25] "ENSG00000186517.13" "ENSG00000143226.13" "ENSG00000173110.7" 
 [28] "ENSG00000244682.7"  "ENSG00000225217.1"  "ENSG00000072694.20"
 [31] "ENSG00000198821.10" "ENSG00000188404.8"  "ENSG00000197959.13"
 [34] "ENSG00000116701.14" "ENSG00000143341.11" "ENSG00000081237.18"
 [37] "ENSG00000116852.14" "ENSG00000118194.18" "ENSG00000143851.15"
 [40] "ENSG00000162894.11" "ENSG00000009790.14"

converting counts to integer mode



[1] "Intercept"               "Mophological.cluster.63"
   [1] "ENSG00000227232.5"  "ENSG00000237973.1"  "ENSG00000248527.1" 
   [4] "ENSG00000225880.5"  "ENSG00000188290.10" "ENSG00000187608.8" 
   [7] "ENSG00000176022.4"  "ENSG00000160087.20" "ENSG00000162572.20"
  [10] "ENSG00000169972.11" "ENSG00000127054.20" "ENSG00000107404.19"
  [13] "ENSG00000175756.13" "ENSG00000221978.11" "ENSG00000224870.6" 
  [16] "ENSG00000242485.5"  "ENSG00000197785.13" "ENSG00000197530.12"
  [19] "ENSG00000269737.2"  "ENSG00000116151.13" "ENSG00000157916.19"
  [22] "ENSG00000157881.13" "ENSG00000227372.11" "ENSG00000130764.9" 
  [25] "ENSG00000069424.14" "ENSG00000116251.9"  "ENSG00000171680.21"
  [28] "ENSG00000162408.10" "ENSG00000116273.5"  "ENSG00000007923.15"
  [31] "ENSG00000171735.18" "ENSG00000049245.12" "ENSG00000049246.14"
  [34] "ENSG00000116285.12" "ENSG00000074800.13" "ENSG00000228526.6" 
  [37] "ENSG00000049239.12" "ENSG00000171603.16" "ENSG00000178585.14"
  [40] "ENSG00000173614.13" "ENSG0

In [25]:
head(cluster_table)

Mophological.cluster.0 Mophological.cluster.1
ENSG00000227232.5  23.092674              14.956715            
ENSG00000279457.4  12.740895               5.641961            
ENSG00000225972.1  -5.473773              21.472882            
ENSG00000225630.1 -10.948954              -6.181880            
ENSG00000237973.1 -38.067027             -18.365856            
ENSG00000229344.1  -8.440806             -32.765781            
                  Mophological.cluster.2 Mophological.cluster.3
ENSG00000227232.5  -0.6887464              6.692536            
ENSG00000279457.4   3.8694956              1.750228            
ENSG00000225972.1 -30.0000000            -30.000000            
ENSG00000225630.1   7.0974352             -8.053532            
ENSG00000237973.1   5.2438468            -28.157696            
ENSG00000229344.1  -5.0024273             13.687167            
                  Mophological.cluster.4 Mophological.cluster.5
ENSG00000227232.5   2.4157528            -8.3409227            
ENSG00000279457.4   3.2883846            -6.3167746            
ENSG00000225972.1 -30.0000000            -0.1132019            
ENSG00000225630.1   0.2519979            -0.9568846            
ENSG00000237973.1 -30.3694829            20.7974072            
ENSG00000229344.1  -2.2276216             6.9213112            
                  Mophological.cluster.6 Mophological.cluster.7
ENSG00000227232.5  3.0364905              -5.495583            
ENSG00000279457.4 -4.0692426              -3.151928            
ENSG00000225972.1 17.0467688             -17.569519            
ENSG00000225630.1  3.9484704              -4.436952            
ENSG00000237973.1 10.7433713              -3.011592            
ENSG00000229344.1 -0.7044187              27.129679            
                  Mophological.cluster.8 Mophological.cluster.9 ⋯
ENSG00000227232.5   1.218346              -6.7257177            ⋯
ENSG00000279457.4  -1.352901               0.3227045            ⋯
ENSG00000225972.1  14.761394             -30.0000000            ⋯
ENSG00000225630.1   2.496602             -19.6445335            ⋯
ENSG00000237973.1  10.813028             -30.0000000            ⋯
ENSG00000229344.1 -14.659046             -19.3638900            ⋯
                  Mophological.cluster.54 Mophological.cluster.55
ENSG00000227232.5 -4.232228                11.325487             
ENSG00000279457.4 -1.860583                 4.013739             
ENSG00000225972.1 13.248473                28.602967             
ENSG00000225630.1  1.170288                -1.322561             
ENSG00000237973.1 -4.866488               -13.932660             
ENSG00000229344.1 -6.398108               -10.315964             
                  Mophological.cluster.56 Mophological.cluster.57
ENSG00000227232.5   3.6700838               6.235699             
ENSG00000279457.4   6.2913037               5.340116             
ENSG00000225972.1 -30.0000000             -30.000000             
ENSG00000225630.1   2.1693757              -5.369283             
ENSG00000237973.1 -22.5214244             -32.066505             
ENSG00000229344.1   0.3904857               1.213891             
                  Mophological.cluster.58 Mophological.cluster.59
ENSG00000227232.5  -1.0383069               7.562584             
ENSG00000279457.4 -11.7717891             -14.403232             
ENSG00000225972.1  30.0000000              30.000000             
ENSG00000225630.1  -5.8277323             -18.679572             
ENSG00000237973.1   0.4466644              30.000000             
ENSG00000229344.1  -9.8375619              30.000000             
                  Mophological.cluster.60 Mophological.cluster.61
ENSG00000227232.5  -8.025373               2.8652868             
ENSG00000279457.4  -3.538594               0.2443175             
ENSG00000225972.1 -13.374338              13.0593670             
ENSG00000225630.1  -4.295670               2.0815449             
ENSG00000237973.1   5.155355              -0.700

In [27]:
cluster_table$"Mophological.cluster.5"

[1]  -8.340922720  -6.316774573  -0.113201859  -0.956884610  20.797407229
    [6]   6.921311215   2.723031557  21.552313287  -4.126498332  -0.713035415
   [11]  -6.077905758  -6.388278881  -0.587530720  -1.410428350  -6.846891542
   [16]  -6.246825738 -11.138679465  -0.318751030  -4.008439240  -1.986863048
   [21]  -6.297407999   4.360217352   7.686501514   3.293492261  -9.688336285
   [26]  -3.515647400   3.756893532  -3.200377608  -3.310627776   1.813484220
   [31]  -1.801269293  -3.033593140   7.045831869  -7.470521457   3.405650664
   [36]   6.035545234   0.061190953  -4.375695489  -0.001307383  -4.949725080
   [41]  -5.915160472   2.853241781   3.294320037  -4.588202364   1.957102033
   [46]  -5.674548111  -2.209994611  -0.361299855   3.343287238  -3.754496270
   [51]  -2.345718459   0.804399840   0.350508189   1.341969794   2.332403327
   [56]  -0.709132560   1.962967969  -1.557748318  -5.628274122  -7.055571135
   [61]   3.270548579   0.884270764 -11.307582442   1.801550991  -8.489617637
   [66]  -7.056752351  -0.882065680  -6.032301251  -4.584870684   3.141937485
   [71]   0.256726236  -8.249162341   2.765507108  -1.796474435  -3.435157109
   [76]   0.356057365   4.306019513   1.324485561  -4.306424651  -0.194457015
   [81]  -6.762992689   0.695085610   2.116335173  -2.478727630  -6.028916641
   [86]   1.978576952  -3.270408919   1.316713740 -11.202703922  -8.031538502
   [91]   2.101484145  -3.450162099   2.250711398  -4.258443573  -2.137755580
   [96]   2.717043900  -0.485218647  -3.141821313  -8.523818030   6.268137413
  [101] -13.748731582  -0.998288722  -1.978909579  12.991073591   4.398970725
  [106]   2.343226531   1.707327448   3.857805194   2.263905643   0.746806349
  [111]  -2.022896710  -2.202339271   6.620742626   1.273537446   3.466604459
  [116]  -3.971383395   0.599575055   1.012144093   9.254489871   0.116447473
  [121]   0.793045552   1.798965240   2.584291935   0.303765033   4.136694524
  [126]  -6.187227149   6.569442058  -2.204236077  -5.254406805   1.511472818
  [131]   5.632169334  -2.971916455  -5.338480587   1.867432959  -1.026404059
  [136]   4.701756468   0.805399969  -2.382781178  30.000000000   1.706334928
  [141]   1.355453739   2.881027142  -2.527892619  -0.980218989   3.460957280
  [146]   7.573101307  -1.008796947  -2.276684462   0.019323806   0.338864707
  [151]   0.065669782  -7.497528302  -0.092212994  -3.210467272  -0.180112340
  [156]  -9.104280199  -3.137144475   1.977315504   0.629454163  -0.433935015
  [161]  -3.138066362   4.898160072  -1.650943462  -5.229079050   0.689392488
  [166]  -1.105497142 -13.234863215   0.850881235  -0.361249995   4.816073234
  [171]   1.077472955  -2.957000132  -4.835999233  -2.991367700  -4.576579228
  [176]  -5.232732561  -5.619327246  -6.445896376  -3.187964545   0.650904286
  [181]   8.725612349   1.635234379  -0.809340203  12.111165851   4.934350538
  [186]  -3.987254560   1.122297165   2.878987416   5.237240644   3.913036683
  [191]   2.917639058   3.634064985   5.908244461  -4.245223399   0.649455101
  [196]  -0.309609911  -4.511941916  -6.005495096  -3.192771681   8.466255550
  [201]  -2.317643177   3.038203071   0.785962126   6.028612509  -5.460564209
  [206]  -4.004381442   1.396234769   1.798405311  -1.771979020   0.564408257
  [211]   7.638620256  -0.330994047  -7.667955080   0.081067653  -0.999921862
  [216]   4.178218264  -2.291642332   1.730083981  12.775315306  16.721961941
  [221]  16.574893094   9.587757862   1.723426425   1.796172621  -4.319342183
  [226]   2.864788943  -0.652740783  -9.239096707  -1.362780790  -2.205966895
  [231]   4.027810904  -0.829090122   2.713580100   2.000994154   4.979054261
  [236]   2.312646969   4.457967146   3.088524258  -4.628658014  -2.653488926
  [241]   0.411857139  -1.204282322   1.810029935   2.613164835   8.854308933
  [246]  -0.972557998  -4.471593869   6.128128716   0.040206133  -6.674068868
  [251]   2.068477305   2.516609835  -0.565531733  -3.461868724   1.332946665
  [256]   1.356712800   1.

In [28]:
pathways <- gmtPathways(system.file(
     "extdata", "c2.cp.reactome.v7.5.1.symbols.gmt", package="fgsea"))

In [63]:
str(head(pathways))
str(head(examplePathways))
str(head(exampleRanks))

List of 6
 $ REACTOME_INTERLEUKIN_6_SIGNALING                                                           : chr [1:11] "JAK2" "TYK2" "CBL" "STAT1" ...
 $ REACTOME_APOPTOSIS                                                                         : chr [1:179] "BAD" "CFLAR" "PSMB1" "PSMC4" ...
 $ REACTOME_HEMOSTASIS                                                                        : chr [1:678] "FGR" "CD99" "TFPI" "KDM1A" ...
 $ REACTOME_INTRINSIC_PATHWAY_FOR_APOPTOSIS                                                   : chr [1:55] "BAD" "BID" "BAK1" "CASP8" ...
 $ REACTOME_MAPK3_ERK1_ACTIVATION                                                             : chr [1:10] "JAK2" "MAPK3" "TYK2" "IL6ST" ...
 $ REACTOME_TRANSLESION_SYNTHESIS_BY_Y_FAMILY_DNA_POLYMERASES_BYPASSES_LESIONS_ON_DNA_TEMPLATE: chr [1:39] "REV3L" "SPRTN" "RFC1" "RFC2" ...
List of 6
 $ 1221633_Meiotic_Synapsis                                                : chr [1:64] "12189" "13006" "15077" "15078" ...
 $ 1368092_Rora

In [67]:
genes <- rna$Description
print(type(genes))

[1] "character"


In [72]:
#create the ranking vector from the cluster 4
#row <- rownames(dataset)

#remplacer le name par description 
#genes <- (rna[1:14050,2])
#print(genes)


v_c5 <- cluster_table$"Mophological.cluster.5"
print(type(v_c5))
names(v_c5) <- rna$Description

str(head(v_c5))

#vector4 <- c(row, v_c4)
#print(vector4)

#names(x) <- value

[1] "double"
 Named num [1:6] -8.341 -6.317 -0.113 -0.957 20.797 ...
 - attr(*, "names")= chr [1:6] "WASH7P" "RP11-34P13.18" "MTND1P23" "MTND2P28" ...


In [76]:
ordered_v_c5 <- sort(v_c5, decreasing = FALSE)
str(head(ordered_v_c5))
ordered_v_c5

 Named num [1:6] -31.7 -30 -30 -30 -30 ...
 - attr(*, "names")= chr [1:6] "STC1" "HIST2H2BF" "HBB" "HBD" ...


STC1           HIST2H2BF                 HBB                 HBD 
      -31.749740224       -30.000000000       -30.000000000       -30.000000000 
                PTH                CHGA               IGHGP              CYP1A1 
      -30.000000000       -30.000000000       -30.000000000       -30.000000000 
               HBA2                HBA1                FOSB                EGR3 
      -30.000000000       -30.000000000       -30.000000000       -29.747115894 
                ADM                ATF3              HSPA1A              HSPA1B 
      -29.709310004       -29.482977232       -27.986318537       -27.260929689 
            FAM180B               ACTG2              SLC2A3           ACTA2-AS1 
      -26.614491642       -26.551942990       -26.157774027       -25.753127784 
              DUSP5               HSPA6             BHLHE40               PTGS2 
      -24.783680898       -24.588518917       -24.234490662       -24.038066040 
              CYR61              SLC5A5                 FOS                 ACE 
      -24.031350169       -23.972383185       -23.944676768       -23.762284897 
              NR4A1                USP6              C8orf4               SFRP4 
      -23.747890867       -23.740659611       -23.285797820       -23.015833978 
               CNN1            SERPINE1                 GEM               PTCH2 
      -22.900896334       -22.470564494       -22.374413526       -21.807881540 
            C1QTNF2               ZFP36               GRIP2                 CA2 
      -21.767240578       -21.681430195       -21.521172586       -21.425282656 
               EGR2           STPG3-AS1            IGHV4-31               CYTL1 
      -21.016425351       -20.735268402       -20.426332617       -20.407723143 
            C1QTNF7              ADGRL3       RP11-757F18.5               RGS11 
      -20.392052675       -20.347005359       -20.199932853       -20.093365248 
              SMOC2               PAMR1                 DES               TPPP3 
      -19.898122516       -19.849078898       -19.627518419       -19.589772094 
              GRIK2                ASPN              DOC2GP                XAF1 
      -19.535402907       -19.522660091       -19.483209621       -19.414035977 
              HMCN2             TNFSF14                 NOV              TSPEAR 
      -19.390620903       -19.361787680       -19.348262666       -19.262694596 
           C12orf75       RP11-588H23.3                RGS8              ABCA10 
      -19.162408493       -19.118494388       -19.110772301       -19.103882453 
              RBM24                RND1              PLPPR4               SFRP2 
      -19.042253764       -18.837853647       -18.764137183       -18.743410318 
               FGF1                GLI1               CCL19                EGR1 
      -18.559120427       -18.552343217       -18.488060266       -18.381346564 
              MYOCD               TNNT3               KCNE3                LEPR 
      -18.210126277       -18.174674317       -18.091463340       -18.047707363 
                JUN               AGBL2        RP11-161M6.2            PPP1R15A 
      -17.955600327       -17.775604450       -17.774432969       -17.626815046 
           CYP4F32P              IFI44L             FAM180A               MYH11 
      -17.571382626       -17.500540498       -17.390505398       -17.346182491 
              F2RL3             NPIPB11               RASA4              DNAJB1 
      -17.139231333       -17.092737495       -17.088230893       -17.024218869 
              RAB26                GNLY                GBP1               HBEGF 
      -16.999231077       -16.926857792       -16.872730826       -16.850274127 
            GALNT16       CH507-42P11.8               CNTN1              MUSTN1 
      -16.818292088       -16.812301259       -16.802981676       -16.771766271 
               PLB1         RP11-13P5.2       RP11-616M22.1              GPR132 
      -16.734156196       -16.643587822       

In [37]:
#data(examplePathways)
#data(exampleRanks)

head(exampleRanks)
head(examplePathways)

170942    109711     18124     12775     72148     16010 
-63.33703 -49.74779 -43.63878 -41.51889 -33.26039 -32.77626

$`1221633_Meiotic_Synapsis`
 [1] "12189"     "13006"     "15077"     "15078"     "15270"     "15512"    
 [7] "16905"     "16906"     "19357"     "20842"     "20843"     "20957"    
[13] "20962"     "21749"     "21750"     "22196"     "23856"     "24061"    
[19] "28113"     "50878"     "56739"     "57321"     "64009"     "66654"    
[25] "69386"     "71846"     "74075"     "77053"     "94244"     "97114"    
[31] "97122"     "97908"     "101185"    "140557"    "223697"    "260423"   
[37] "319148"    "319149"    "319150"    "319151"    "319152"    "319153"   
[43] "319154"    "319155"    "319156"    "319157"    "319158"    "319159"   
[49] "319160"    "319161"    "319565"    "320332"    "320558"    "326619"   
[55] "326620"    "360198"    "497652"    "544973"    "625328"    "667250"   
[61] "100041230" "102641229" "102641751" "102642045"

$`1368092_Rora_activates_gene_expression`
[1] "11865"  "12753"  "12894"  "18143"  "19017"  "19883"  "20787"  "217166"
[9] "328572"

$`1368110_Bmal1:Clock,Npas2_activates_circadian_gene_expression`
 [1] "11865"  "11998"  "12753"  "12952"  "12953"  "13170"  "14068"  "18143" 
 [9] "18626"  "18627"  "19013"  "19883"  "20893"  "59027"  "79362"  "217166"

$`1445146_Translocation_of_Glut4_to_the_Plasma_Membrane`
 [1] "11461"     "11465"     "11651"     "11652"     "12313"     "12314"    
 [7] "12315"     "16568"     "16569"     "16579"     "17274"     "17884"    
[13] "17886"     "17913"     "17918"     "19079"     "19082"     "19325"    
[19] "19341"     "20336"     "20528"     "20619"     "20909"     "20912"    
[25] "22318"     "22627"     "22628"     "22629"     "22630"     "22631"    
[31] "53413"     "54401"     "55948"     "56044"     "57915"     "66482"    
[37] "68328"     "68365"     "68938"     "69940"     "102058"    "105504"   
[43] "107371"    "108079"    "108097"    "108099"    "210789"    "211446"   
[49] "240028"    "241113"    "241694"    "100039786" "102634437" "102641200"
[55] "102641764"

$`186574_Endocrine-committed_Ngn3+_progenitor_cells`
[1] "18012" "18088" "18506" "53626"

$`186589_Late_stage_branching_morphogenesis_pancreatic_bud_precursor_cells`
[1] "11925"  "15205"  "21410"  "246086"

In [52]:
print(type(exampleRanks))
exampleRanks[1]
exampleRanks[2]

[1] "double"


170942 
-63.33703

109711 
-49.74779